In [3]:
using Strategems, Indicators, Temporal, Dates

In [24]:
# define universe and gather data
# assets = ["CHRIS/CME_CL1", "CHRIS/CME_RB1"]
# universe = Universe(assets)
function datasource(asset::String; save_downloads::Bool=true)::TS
    savedata_path = joinpath(dirname(pathof(Strategems)), "..", "data", "$asset.csv")
    print(savedata_path)
    if isfile(savedata_path)
        return Temporal.tsread(savedata_path)
    else
        X = quandl(asset)
        if save_downloads
            if !isdir(dirname(savedata_path))
                mkdir(dirname(savedata_path))
            end
            Temporal.tswrite(X, savedata_path)
        end
        return X
    end
end

assets = [String("C:/Users/s154857/Documents/Bayesian_trader/Data")]
universe = Universe(assets)
#   ETHUSDT-1m-2021-06-06
function datasource(dataroot_path::String, file_name::String="CME_CL1.csv")
    savedata_path = joinpath(dataroot_path, file_name)
    print(dirname(pathof(Strategems)))
    print(savedata_path)
    return Temporal.tsread(savedata_path)
end
    
gather!(universe, source=datasource)

# define indicators and parameter space
arg_names     = [:fastlimit, :slowlimit]
arg_defaults  = [0.5, 0.05]
arg_ranges    = [0.01:0.01:0.99, 0.01:0.01:0.99]
paramset      = ParameterSet(arg_names, arg_defaults, arg_ranges)
f(x; args...) = Indicators.mama(x; args...)
indicator     = Indicator(f, paramset)

# define signals that will trigger trading decisions
# note the uparrow infix operator is defined to simplify one variable crossing over another
# (similarly for the downarrow infix operator for crossing under)
siglong  = @signal MAMA ↑ FAMA
sigshort = @signal MAMA ↓ FAMA
sigexit  = @signal MAMA == FAMA

# define the trading rules
longrule  = @rule siglong → long 100
shortrule = @rule sigshort → short 100
exitrule  = @rule sigexit → liquidate 1.0
rules     = (longrule, shortrule, exitrule)

# run strategy
strat = Strategy(universe, indicator, rules)
backtest!(strat)
optimize!(strat, samples=0)  # randomly sample the parameter space (0 -> use all combinations)

# cumulative pnl for each combination of the parameter space
strat.backtest.optimization

# visualizing results with the Plots.jl package
using Plots
gr()
(x, y, z) = (strat.backtest.optimization[:,i] for i in 1:3)
surface(x, y, z)

C:\Users\s154857\.julia\packages\Strategems\WM60M\srcC:/Users/s154857/Documents/Bayesian_trader/Data\CME_CL1.csv

Optimizing Backtest100%|████████████████████████████████| Time: 0:04:399mm9m9m
┌ Info: Precompiling Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80]
└ @ Base loading.jl:1278
